<a href="https://colab.research.google.com/github/alozy15/A_B-Testing/blob/master/timeseries_fcst.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Time Series Analytics

In [ ]:
pip install pmdarima


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.4 MB 3.2 MB/s 
     |████████████████████████████████| 9.8 MB 30.0 MB/s 
  Attempting uninstall: statsmodels
    Found existing installation: statsmodels 0.10.2
    Uninstalling statsmodels-0.10.2:
      Successfully uninstalled statsmodels-0.10.2


In [ ]:
pip install pygsheets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 147 kB 3.7 MB/s 


In [ ]:
pip install neuralprophet


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 74 kB 2.1 MB/s 


In [ ]:
def date_index(df):        
    '''pass dataframe and set datetime index'''
    if df.columns.str.contains('date').any() == True:
        df.set_index('date', inplace = True)
        
    if df.columns.str.contains('Date').any() == True:
        df.set_index('Date', inplace = True)
    
    if df.columns.str.contains('day_dt').any() == True:
        df.set_index('day_dt', inplace = True)

    if df.columns.str.contains('ds').any() == True:
        df.set_index('ds', inplace = True)
        
    #else:
     #   print('There does not appear to be a date like column')
    
    return df

In [ ]:
pip install prophet

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:


from prophet import Prophet
from prophet.plot import plot
from prophet.plot import add_changepoints_to_plot
from prophet.plot import plot_plotly, plot_components_plotly
from prophet.diagnostics import cross_validation
from prophet.diagnostics import performance_metrics
from prophet.plot import plot_cross_validation_metric
from neuralprophet import NeuralProphet
#import pyramid
import pmdarima as pm

from pmdarima.arima import auto_arima
#from pyramid.arima.stationarity import ADFTest
import plotly.graph_objects as go

import statsmodels.api as sm
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import adfuller
#from statsmodels.tsa.arima_model import ARIMA

from sklearn.model_selection import TimeSeriesSplit
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier, GradientBoostingRegressor
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV, train_test_split, cross_validate
from sklearn.linear_model import LinearRegression, RidgeCV,  LassoCV
from sklearn import svm
from sklearn.model_selection import cross_val_score

#import pytorch

import keras
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import LSTM


import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import os
import datetime
from datetime import date
import holidays
from datetime import timedelta
from pandas.tseries.offsets import MonthEnd
import warnings
import seaborn as sns
import pygsheets 
import itertools
import functools
warnings.filterwarnings('ignore')
print( os.getcwd())

import google.auth
import google.cloud as gcp
from google_auth_oauthlib import flow
from google.cloud import storage
from google.cloud import bigquery
from oauth2client import file 

/content


In [ ]:
from google.colab import auth
auth.authenticate_user()

In [ ]:
#@title Default title text
# Replace project ID with your project
#project_id = 'rv-mt-adtech-data-prod'
#sample_count = 2000

#row_count = pd.io.gbq.read_gbq('''
 # SELECT  *
    # Replace i-cmg-tools.colab_test.table_1 with your BQ table or dataset
 # FROM `dw_programmatic.burt_programmatic_kpi_historicals`
#''', project_id=project_id).total[0]

#df = pd.io.gbq.read_gbq(f'''
 # SELECT
  #  *
    # Replace i-cmg-tools.colab_test.table_1 with your BQ table or dataset
 # FROM `i-cmg-tools.colab_test.table_1`
 # WHERE RAND() < {sample_count}/{row_count}
#''', project_id=project_id)

In [ ]:
# Replace project ID with your project
project_id = 'rv-mt-adtech-data-prod'

df = pd.io.gbq.read_gbq("""
WITH daily_rev AS
(
SELECT 
CAST(day_dt AS DATE) AS day_dt,
CASE WHEN report_site_nm = 'Games' THEN 'Game Spot'
WHEN report_site_nm = 'TV.com' THEN 'TV'
ELSE report_site_nm END AS report_site_nm,

CASE WHEN (report_site_nm) = 'CNET' THEN 'CNET_all_verticals'
WHEN (report_site_nm) = 'Download' THEN 'CNET_all_verticals'
WHEN report_site_nm IN ('Comic Vine', 'Game FAQs', 'Game Spot', 'Giant Bomb', 'Games') THEN 'Games'
WHEN report_site_nm IN ('Tech Republic', 'ZD Net') THEN 'B2B'
WHEN report_site_nm IN('Chowhound', 'Metacritic','TV.com','TV Guide', 'Metrolyrics', 'Guide') THEN 'Media&Entertainment'
ELSE 'CNET(all_verticals)' END AS vertical,

#CASE WHEN kpi_product_nm LIKE('%Rev%') THEN 'US_Rev Initiatives'
#WHEN kpi_product_nm LIKE ('%Open%') THEN 'US'
#ELSE 'other' END AS region,
#'CMGkpihist' AS datasource,

ROUND(CAST(SUM(revenue_amt) AS DECIMAL),2) As revenue

FROM dw_programmatic.burt_programmatic_kpi_historicals
WHERE day_dt >= '2019-01-01'
AND hb_wrapper_desc NOT IN ('Ad Block Recovered', 'House', 'Low CPM Mop')
AND platform_group_nm <> 'unmap'
#AND platform_group_nm IS NOT NULL
#AND US_KPI = 'Y'
AND kpi_product_nm IN('Open Exchange', 'Revenue Initiatives')
AND report_site_nm <> 'Tech Republic'
AND report_site_nm <> 'Next Advisor'
AND report_site_nm <> 'Bank Rate'
AND report_site_nm <>'unmap'
AND region_nm <>'unmap'
GROUP BY 1,2,3#,4
ORDER BY day_dt DESC
)

SELECT day_dt,
report_site_nm,
vertical,
SUM(revenue) AS revenue
FROM daily_rev
GROUP BY 1,2,3
ORDER BY 1


""", project_id=project_id)#.to_dataframe()
df['revenue'] = df.revenue.astype(float)
df['day_dt'] = pd.to_datetime(df['day_dt'])
df = date_index(df).sort_index()

df.tail(10)

df2 = df.copy()

In [ ]:
df2.head()

report_site_nm             vertical  revenue
day_dt                                                 
2019-11-01     Giant Bomb                Games    92.46
2019-11-01       Download   CNET_all_verticals  2509.77
2019-11-01      Game FAQs                Games  1955.41
2019-11-01     Metacritic  Media&Entertainment  3885.82
2019-11-01      Chowhound  Media&Entertainment   822.73

In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 12946 entries, 2019-11-01 to 2022-08-03
Data columns (total 3 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   report_site_nm  12946 non-null  object 
 1   vertical        12946 non-null  object 
 2   revenue         12946 non-null  float64
dtypes: float64(1), object(2)
memory usage: 404.6+ KB


# Prophet Modeling

## Defs

In [ ]:
verticals = list(df.vertical.unique())
sites = list(df.report_site_nm.unique())



def comp_summary(df, date1,date2):
  summary_df = df.loc[date1:date2].resample(rule = 'M').sum()
  summary_df['difference'] = summary_df.prophet_fcst_revenue - summary_df.revenue 
  summary_df['%_diff'] = (((summary_df.prophet_fcst_revenue /summary_df.revenue ).round(5))-1).round(2)

  return summary_df


def prophet_vertical_split(bu):
    '''creates a seperate df for each business unit in verticals. keeps only numerical columns and resamples for daily groupings'''
    #split_df = df[df['vertical'] == bu].select_dtypes(include = ['float64'])
    split_df = df[df['vertical'] == bu].resample(rule = 'D').sum()
    split_df.rename(index = {0:'ds'}, columns={'day_dt':'ds','revenue':'y'},inplace=True)
    split_df.index.names = ['day_dt']
    split_df['ds'] = split_df.index    
    split_df = split_df.sort_index()

    #split_df = df.resample(rule = 'D').sum()
    
    return split_df

    
for bu in verticals:
    '''to call a vertical...B2B'''
    globals()[str(bu).replace("&","_")] = prophet_vertical_split(bu)
    


def prophet_site_split(site):
    '''creates a seperate df for each business unit in verticals. keeps only numerical columns and resamples for daily groupings'''
    #split_df = df[df['vertical'] == bu].select_dtypes(include = ['float64'])
    split_df = df[df['report_site_nm'] == site].resample(rule = 'D').sum()
    #split_df = df.resample(rule = 'D').sum()
    split_df.rename(index = {0:'ds'}, columns={'day_dt':'ds','revenue':'y'},inplace=True)
    split_df.index.names = ['day_dt']    
    split_df['ds'] = split_df.index    
    split_df = split_df.sort_index()

    
    return split_df

    
for site in sites:
    '''to call a site...CNET'''
    globals()[str(site).replace(" ","_")] = prophet_site_split(site)  
    
      
#The order of vertical splits and vertical split names must be in the same order
site_splits = [Game_FAQs, ZD_Net, Chowhound, CNET, Giant_Bomb, Download, TV_Guide, Comic_Vine, TV, Game_Spot, Metacritic, Metrolyrics]
site_splits_names = ['Game_FAQs', 'ZD_Net', 'Chowhound', 'CNET', 'Giant_Bomb', 'Download', 'TV_Guide', 'Comic_Vine', 'TV', 'Game_Spot', 'Metacritic', 'Metrolyrics']
vertical_splits = [B2B, Media_Entertainment, CNET_all_verticals, Games]
vertical_splits_names = ["B2B", "Media_Entertainment", "CNET_all_verticals", "Games"]
    

In [ ]:
#to call vertical or site just enter vertical/site name of the data you want to view...etc Game_Spot
#vertical call
CNET_all_verticals

y         ds
day_dt                         
2019-11-01  37592.54 2019-11-01
2019-11-02  35206.57 2019-11-02
2019-11-03  43993.80 2019-11-03
2019-11-04  40072.37 2019-11-04
2019-11-05  32818.73 2019-11-05
...              ...        ...
2022-07-30  21545.13 2022-07-30
2022-07-31  21039.82 2022-07-31
2022-08-01  20827.49 2022-08-01
2022-08-02  20525.41 2022-08-02
2022-08-03  19665.09 2022-08-03

[1007 rows x 2 columns]

In [ ]:
#site call
CNET

y         ds
day_dt                         
2019-11-01  35082.77 2019-11-01
2019-11-02  32779.67 2019-11-02
2019-11-03  41536.35 2019-11-03
2019-11-04  37729.36 2019-11-04
2019-11-05  30692.96 2019-11-05
...              ...        ...
2022-07-30  18993.76 2022-07-30
2022-07-31  18484.33 2022-07-31
2022-08-01  17928.62 2022-08-01
2022-08-02  17568.74 2022-08-02
2022-08-03  16801.46 2022-08-03

[1007 rows x 2 columns]

In [ ]:
#printing holidays and turn to DF to implement with prophet

#holiday_years = [2021, 2022]
holiday_years = [2021]
holidays.UnitedStates()
for holiday in holidays.US(years = holiday_years).items():
    display(list(holiday))

holidayz = pd.DataFrame(list(holidays.UnitedStates(years = holiday_years).items()), columns = ['ds', 'holiday'])



superbowls = pd.DataFrame({
  'holiday': 'Superbowl',
  'ds': pd.to_datetime(['2020-02-02', '2021-02-07', '2022-02-06', '2023-02-05', '2024-02-04', '2020-02-02']),
  'lower_window': -3,#covers weekend leading up to Superbowl
  'upper_window': 1,
})

black_friday = pd.DataFrame({
    'holiday' : 'Black Friday',
    'ds': pd.to_datetime(['2020-11-27', '2021-11-26', '2022-11-25', '2023-11-24', '2024-11-29','2024-11-28']),
    'lower_window' : 0, #we already have thanksgiving
    'upper_window' : 3, #covers the weekend leading up to and including cyber monday
})

#look to add CES and Comic-Con

#all_holidayz = pd.concat((holidayz, superbowls, black_friday ))
#all_holidayz = pd.concat((holidayz, superbowls, black_friday ))
all_holidayz = pd.concat(([holidayz,black_friday]))

#fills in the NaN values for lower and upper windows with 0
all_holidayz = all_holidayz.fillna(0)    

[datetime.date(2021, 1, 1), "New Year's Day"]

[datetime.date(2021, 12, 31), "New Year's Day (Observed)"]

[datetime.date(2021, 1, 18), 'Martin Luther King Jr. Day']

[datetime.date(2021, 2, 15), "Washington's Birthday"]

[datetime.date(2021, 5, 31), 'Memorial Day']

...

[datetime.date(2021, 10, 11), 'Columbus Day']

[datetime.date(2021, 11, 11), 'Veterans Day']

[datetime.date(2021, 11, 25), 'Thanksgiving']

[datetime.date(2021, 12, 25), 'Christmas Day']

[datetime.date(2021, 12, 24), 'Christmas Day (Observed)']

In [ ]:
#creation of prophet models.  Will loop through vertical/site splits list.  Name is assigned using vertical_split_names list.  The order of vertical splits and vertical split names must be in the same order


#define the forecasting model parameters, trend = logistic growth, yearly seasonality = multiplicative, no holiday parameter
#model_params = {"daily_seasonality": False, "weekly_seasonality": False, "yearly_seasonality": True, "seasonality_mode": "multiplicative", "growth": "linear"}

#model = Prophet(holidays = all_holidayz, yearly_seasonality= False, daily_seasonality= False, weekly_seasonality= False, growth = 'linear')


#model = Prophet(holidays = all_holidayz)
#model.add_country_holidays(country_name = 'US')

# cap and floor if using logistic growth
#cnet_df['cap'] = 200000
#cnet_df['floor']  = 1000


#prophet_prediction = model.fit(cnet_df)

#prophet_prediction



logistic_prophet_model_dict = {}
linear_prophet_model_dict = {}


#vertical_splits
#for index, vertical in enumerate(vertical_splits):

#site_splits
for index, vertical in enumerate(site_splits):

    neural_model = NeuralProphet()


    #cap and floor are used for logistic growth.  
    vertical['cap'] = 200000
    vertical['floor'] = 1000

    #rpt_site['cap'] = 200000
    #rpt_site['floor'] = 1000

    model = Prophet(holidays = all_holidayz, yearly_seasonality= False, daily_seasonality= False, weekly_seasonality= False, growth = 'logistic').add_seasonality(name = 'yearly', period = 365.25, fourier_order= 100).add_seasonality(name = 'quarterly', period = 365.25/4, fourier_order= 100).add_seasonality(name = 'weekly', period = 7, fourier_order= 50)
    #prophet_model_dict[f'prophet_{vertical_splits_names[index]}_model'] = model.fit(vertical)

    linear_model = Prophet(holidays= all_holidayz)

    #create prediction dataframes with forward range of dates
    #future_dates = model.make_future_dataframe(periods = 95, freq = "D")
    
    

    #vertical_split dict, need to select this line or line below.  depends if forecasting for verticals or individual sites
    #prophet_model_dict[f'prophet_{vertical_splits_names[index]}_model'] = model.fit(vertical)

    #site split dict
    logistic_prophet_model_dict[f'prophet_{site_splits_names[index]}_logistic_model'] = model.fit(vertical)
    linear_prophet_model_dict[f'prophet_{site_splits_names[index]}_linear_model'] = linear_model.fit(vertical)


    #prophet_prediction = model.predict(future_dates)
  
    #prophet_prediction = prophet_prediction.astype(int)
    #prophet_prediction['ds'] = pd.to_datetime(prophet_prediction['ds'])
    #print(f"******Summary for {vertical.keys()} prophet model ********",'\n')
    #display(prophet_prediction.tail(5))

    
for key in logistic_prophet_model_dict.keys():
  print(f"******Summary for {key} logistic prophet model ********")
  print(logistic_prophet_model_dict[key],'\n')

print ("Dict key-value within logistic prophet_model_dict are : ")
for key, value in logistic_prophet_model_dict.items():
    print (key,':', value,'\n')

print('\n','----------------------------------------------------------')    

for key in linear_prophet_model_dict.keys():
  print(f"******Summary for {key} linear prophet model ********")
  print(linear_prophet_model_dict[key],'\n')

print ("Dict key-value within linear prophet_model_dict are : ")
for key, value in linear_prophet_model_dict.items():
    print (key,':', value,'\n')




17:55:13 - cmdstanpy - INFO - Chain [1] start processing
17:55:14 - cmdstanpy - INFO - Chain [1] done processing
17:55:14 - cmdstanpy - INFO - Chain [1] start processing
17:55:14 - cmdstanpy - INFO - Chain [1] done processing
17:55:15 - cmdstanpy - INFO - Chain [1] start processing
17:55:15 - cmdstanpy - INFO - Chain [1] done processing
17:55:15 - cmdstanpy - INFO - Chain [1] start processing
17:55:16 - cmdstanpy - INFO - Chain [1] done processing
17:55:16 - cmdstanpy - INFO - Chain [1] start processing
17:55:17 - cmdstanpy - INFO - Chain [1] done processing
17:55:17 - cmdstanpy - INFO - Chain [1] start processing
17:55:17 - cmdstanpy - INFO - Chain [1] done processing
17:55:17 - cmdstanpy - INFO - Chain [1] start processing
17:55:20 - cmdstanpy - INFO - Chain [1] done processing
17:55:20 - cmdstanpy - INFO - Chain [1] start processing
17:55:21 - cmdstanpy - INFO - Chain [1] done processing
17:55:21 - cmdstanpy - INFO - Chain [1] start processing
17:55:22 - cmdstanpy - INFO - Chain [1]

******Summary for prophet_Game_FAQs_logistic_model logistic prophet model ********

******Summary for prophet_ZD_Net_logistic_model logistic prophet model ********

******Summary for prophet_Chowhound_logistic_model logistic prophet model ********

******Summary for prophet_CNET_logistic_model logistic prophet model ********

******Summary for prophet_Giant_Bomb_logistic_model logistic prophet model ********

******Summary for prophet_Download_logistic_model logistic prophet model ********

******Summary for prophet_TV_Guide_logistic_model logistic prophet model ********

******Summary for prophet_Comic_Vine_logistic_model logistic prophet model ********

******Summary for prophet_TV_logistic_model logistic prophet model ********

******Summary for prophet_Game_Spot_logistic_model logistic prophet model ********

******Summary for prophet_Metacritic_logistic_model logistic prophet model ********

******Summary for prophet_Metrolyrics_logistic_model logistic prophet model ********

Dict

## Prophet Logistic

In [ ]:
fit_predict_dict = {}
for prophet_model_key in logistic_prophet_model_dict.keys():
  model = logistic_prophet_model_dict[prophet_model_key]
  #print(model)
  #print('\n')

  #create prediction dataframes with forward range of dates
  future_dates = model.make_future_dataframe(periods = 95, freq = "D")
  #display(future_dates)

  #cap and floor are used for logistic growth.  
  future_dates['cap'] = 200000
  future_dates['floor'] = 1000

  prophet_prediction = model.predict(future_dates)

  #making sure logistic takes all the negative values and returns absolute value
  prophet_prediction['yhat'] = prophet_prediction['yhat'].abs()

  prophet_prediction = prophet_prediction.astype(int)
  prophet_prediction['ds'] = pd.to_datetime(prophet_prediction['ds'])
  #print(f"******Summary for {prophet_model_key} prophet model ********",'\n')
  #display(prophet_prediction.tail(5))

  #plots
  print(f"******Summary graphs {prophet_model_key}********",'\n')
  display(plot_plotly(model, prophet_prediction, figsize=(3000,1000)))
  print('\n\n')
  display(plot_components_plotly(model, prophet_prediction,figsize=(3000,1000)))
  print('\n\n')

  print(f"******Summary for {prophet_model_key}********",'\n')
  prophet_prediction = prophet_prediction.reindex(['ds','yhat'], axis = 1)
  prophet_prediction.rename(columns={'ds':'date','yhat':'prophet_fcst_revenue'},inplace=True)

  prophet_prediction['vertical'] = prophet_model_key
  prophet_prediction.set_index('date', inplace = True)
  display(prophet_prediction.tail(5))
  
  fit_predict_dict[prophet_model_key]= prophet_prediction
  print('\n\n')



    

******Summary graphs prophet_Game_FAQs_logistic_model******** 






******Summary for prophet_Game_FAQs_logistic_model******** 



prophet_fcst_revenue                          vertical
date                                                              
2022-11-02                  1706  prophet_Game_FAQs_logistic_model
2022-11-03                  2332  prophet_Game_FAQs_logistic_model
2022-11-04                  2542  prophet_Game_FAQs_logistic_model
2022-11-05                  2776  prophet_Game_FAQs_logistic_model
2022-11-06                  2852  prophet_Game_FAQs_logistic_model




******Summary graphs prophet_ZD_Net_logistic_model******** 






******Summary for prophet_ZD_Net_logistic_model******** 



...




******Summary for prophet_Metacritic_logistic_model******** 



prophet_fcst_revenue                           vertical
date                                                               
2022-11-02                  2221  prophet_Metacritic_logistic_model
2022-11-03                  2320  prophet_Metacritic_logistic_model
2022-11-04                  2993  prophet_Metacritic_logistic_model
2022-11-05                  2440  prophet_Metacritic_logistic_model
2022-11-06                  1896  prophet_Metacritic_logistic_model




******Summary graphs prophet_Metrolyrics_logistic_model******** 






******Summary for prophet_Metrolyrics_logistic_model******** 



prophet_fcst_revenue                            vertical
date                                                                
2021-10-30                   481  prophet_Metrolyrics_logistic_model
2021-10-31                   362  prophet_Metrolyrics_logistic_model
2021-11-01                   285  prophet_Metrolyrics_logistic_model
2021-11-02                   301  prophet_Metrolyrics_logistic_model
2021-11-03                   332  prophet_Metrolyrics_logistic_model

In [ ]:
#pd.set_option('display.max_rows', 100)
print ("Dict key-value within fit_predict_dict are : ")
for key, value in fit_predict_dict.items():
  display(key, value)
  print('\n')

Dict key-value within fit_predict_dict are : 


'prophet_Game_FAQs_logistic_model'

prophet_fcst_revenue                          vertical
date                                                              
2019-11-01                  1681  prophet_Game_FAQs_logistic_model
2019-11-02                  2257  prophet_Game_FAQs_logistic_model
2019-11-03                  2747  prophet_Game_FAQs_logistic_model
2019-11-04                  2270  prophet_Game_FAQs_logistic_model
2019-11-05                  2172  prophet_Game_FAQs_logistic_model
...                          ...                               ...
2022-11-02                  1706  prophet_Game_FAQs_logistic_model
2022-11-03                  2332  prophet_Game_FAQs_logistic_model
2022-11-04                  2542  prophet_Game_FAQs_logistic_model
2022-11-05                  2776  prophet_Game_FAQs_logistic_model
2022-11-06                  2852  prophet_Game_FAQs_logistic_model

[1102 rows x 2 columns]

'prophet_ZD_Net_logistic_model'

prophet_fcst_revenue                       vertical
date                                                           
2019-11-01                  4889  prophet_ZD_Net_logistic_model
2019-11-02                  2637  prophet_ZD_Net_logistic_model
2019-11-03                  5534  prophet_ZD_Net_logistic_model
2019-11-04                  7680  prophet_ZD_Net_logistic_model
2019-11-05                  4566  prophet_ZD_Net_logistic_model
...                          ...                            ...
2022-11-02                  4312  prophet_ZD_Net_logistic_model
2022-11-03                  5420  prophet_ZD_Net_logistic_model
2022-11-04                  5464  prophet_ZD_Net_logistic_model
2022-11-05                  4575  prophet_ZD_Net_logistic_model
2022-11-06                 12585  prophet_ZD_Net_logistic_model

[1102 rows x 2 columns]

...

prophet_fcst_revenue                          vertical
date                                                              
2019-11-01                  9272  prophet_Game_Spot_logistic_model
2019-11-02                 46593  prophet_Game_Spot_logistic_model
2019-11-03                 47307  prophet_Game_Spot_logistic_model
2019-11-04                 50036  prophet_Game_Spot_logistic_model
2019-11-05                 10194  prophet_Game_Spot_logistic_model
...                          ...                               ...
2022-11-02                 66460  prophet_Game_Spot_logistic_model
2022-11-03                 91617  prophet_Game_Spot_logistic_model
2022-11-04                 16666  prophet_Game_Spot_logistic_model
2022-11-05                 28811  prophet_Game_Spot_logistic_model
2022-11-06                 12044  prophet_Game_Spot_logistic_model

[1102 rows x 2 columns]

'prophet_Metacritic_logistic_model'

prophet_fcst_revenue                           vertical
date                                                               
2019-11-01                  2741  prophet_Metacritic_logistic_model
2019-11-02                  2422  prophet_Metacritic_logistic_model
2019-11-03                  2180  prophet_Metacritic_logistic_model
2019-11-04                  2250  prophet_Metacritic_logistic_model
2019-11-05                  2309  prophet_Metacritic_logistic_model
...                          ...                                ...
2022-11-02                  2221  prophet_Metacritic_logistic_model
2022-11-03                  2320  prophet_Metacritic_logistic_model
2022-11-04                  2993  prophet_Metacritic_logistic_model
2022-11-05                  2440  prophet_Metacritic_logistic_model
2022-11-06                  1896  prophet_Metacritic_logistic_model

[1102 rows x 2 columns]

'prophet_Metrolyrics_logistic_model'

prophet_fcst_revenue                            vertical
date                                                                
2019-11-01                   583  prophet_Metrolyrics_logistic_model
2019-11-02                   581  prophet_Metrolyrics_logistic_model
2019-11-03                   601  prophet_Metrolyrics_logistic_model
2019-11-04                   537  prophet_Metrolyrics_logistic_model
2019-11-05                   503  prophet_Metrolyrics_logistic_model
...                          ...                                 ...
2021-10-30                   481  prophet_Metrolyrics_logistic_model
2021-10-31                   362  prophet_Metrolyrics_logistic_model
2021-11-01                   285  prophet_Metrolyrics_logistic_model
2021-11-02                   301  prophet_Metrolyrics_logistic_model
2021-11-03                   332  prophet_Metrolyrics_logistic_model

[734 rows x 2 columns]

In [ ]:

pd.set_option('display.max_rows', 10)


#combines all the prediction dfs vertically
merge = functools.partial(pd.merge, left_index = True, right_index = True, how = 'inner')
df_stack = functools.reduce(merge, fit_predict_dict.values())
df_stack.rename(columns = {'prophet_fcst_revenue_x': 'prophet_fcst_revenue', 'prophet_fcst_revenue_y': 'prophet_fcst_revenue', 'vertical_x':'vertical', 'vertical_y':' vertical'  }, inplace = True)
#df['date'] = df.index
#df= df.reset_index()

#df = pd.pivot_table(df, index =['vertical'], columns = 'prophet_fcst_revenue', aggfunc = np.sum, margins = True, margins_name = 'Total', fill_value = 0).round(2)
df_stack

prophet_fcst_revenue                          vertical  \
date                                                                 
2019-11-01                  1681  prophet_Game_FAQs_logistic_model   
2019-11-02                  2257  prophet_Game_FAQs_logistic_model   
2019-11-03                  2747  prophet_Game_FAQs_logistic_model   
2019-11-04                  2270  prophet_Game_FAQs_logistic_model   
2019-11-05                  2172  prophet_Game_FAQs_logistic_model   
...                          ...                               ...   
2021-10-30                  2182  prophet_Game_FAQs_logistic_model   
2021-10-31                  2175  prophet_Game_FAQs_logistic_model   
2021-11-01                  2058  prophet_Game_FAQs_logistic_model   
2021-11-02                  1922  prophet_Game_FAQs_logistic_model   
2021-11-03                  2312  prophet_Game_FAQs_logistic_model   

            prophet_fcst_revenue                       vertical  \
date                                                              
2019-11-01                  4889  prophet_ZD_Net_logistic_model   
2019-11-02                  2637  prophet_ZD_Net_logistic_model   
2019-11-03                  5534  prophet_ZD_Net_logistic_model   
2019-11-04                  7680  prophet_ZD_Net_logistic_model   
2019-11-05                  4566  prophet_ZD_Net_logistic_model   
...                          ...                            ...   
2021-10-30                  5004  prophet_ZD_Net_logistic_model   
2021-10-31                 10009  prophet_ZD_Net_logistic_model   
2021-11-01                  7758  prophet_ZD_Net_logistic_model   
2021-11-02                  6762  prophet_ZD_Net_logistic_model   
2021-11-03                  7684  prophet_ZD_Net_logistic_model   

            prophet_fcst_revenue                          vertical  \
date                                                                 
2019-11-01                   514  prophet_Chowhound_logistic_model   
2019-11-02                   765  prophet_Chowhound_logistic_model   
2019-11-03                   797  prophet_Chowhound_logistic_model   
2019-11-04                   587  prophet_Chowhound_logistic_model   
2019-11-05                   484  prophet_Chowhound_logistic_model   
...                          ...                               ...   
2021-10-30                   472  prophet_Chowhound_logistic_model   
2021-10-31                   599  prophet_Chowhound_logistic_model   
2021-11-01                   603  prophet_Chowhound_logistic_model   
2021-11-02                   566  prophet_Chowhound_logistic_model   
2021-11-03                   627  prophet_Chowhound_logistic_model   

            prophet_fcst_revenue                     vertical  \
date                                                            
2019-11-01                 34601  prophet_CNET_logistic_model   
2019-11-02                 41344  prophet_CNET_logistic_model   
2019-11-03                 46669  prophet_CNET_logistic_model   
2019-11-04                 34670  prophet_CNET_logistic_model   
2019-11-05                 33640  prophet_CNET_logistic_model   
...                          ...                          ...   
2021-10-30                  6360  prophet_CNET_logistic_model   
2021-10-31                 14643  prophet_CNET_logistic_model   
2021-11-01                 18616  prophet_CNET_logistic_model   
2021-11-02                 14560  prophet_CNET_logistic_model   
2021-11-03                 20835  prophet_CNET_logistic_model   

            prophet_fcst_revenue                           vertical  ...  \
date                                                                 ...   
2019-11-01                    77  prophet_Giant_Bomb_logistic_model  ...   
2019-11-02                    83  prophet_Giant_Bomb_logistic_model  ...   
2019-11-03                   102  prophet_Giant_Bomb_logistic_model  ...   
2019-11-04                    77  prophet_Giant_Bomb_logistic_model  ...   
2019-11-05      

In [ ]:
for key, value in fit_predict_dict.items():
  value = value.rename(columns = {'prophet_fcst_revenue_x': 'prophet_fcst_revenue', 'prophet_fcst_revenue_y': 'prophet_fcst_revenue', 'vertical_x':'vertical', 'vertical_y':' vertical'  })
  #display(pd.merge(value, value, left_on = value.index, right_on = value.index, how = 'inner'))
  display(value)
  

prophet_fcst_revenue                          vertical
date                                                              
2019-11-01                  1681  prophet_Game_FAQs_logistic_model
2019-11-02                  2257  prophet_Game_FAQs_logistic_model
2019-11-03                  2747  prophet_Game_FAQs_logistic_model
2019-11-04                  2270  prophet_Game_FAQs_logistic_model
2019-11-05                  2172  prophet_Game_FAQs_logistic_model
...                          ...                               ...
2022-11-02                  1706  prophet_Game_FAQs_logistic_model
2022-11-03                  2332  prophet_Game_FAQs_logistic_model
2022-11-04                  2542  prophet_Game_FAQs_logistic_model
2022-11-05                  2776  prophet_Game_FAQs_logistic_model
2022-11-06                  2852  prophet_Game_FAQs_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                       vertical
date                                                           
2019-11-01                  4889  prophet_ZD_Net_logistic_model
2019-11-02                  2637  prophet_ZD_Net_logistic_model
2019-11-03                  5534  prophet_ZD_Net_logistic_model
2019-11-04                  7680  prophet_ZD_Net_logistic_model
2019-11-05                  4566  prophet_ZD_Net_logistic_model
...                          ...                            ...
2022-11-02                  4312  prophet_ZD_Net_logistic_model
2022-11-03                  5420  prophet_ZD_Net_logistic_model
2022-11-04                  5464  prophet_ZD_Net_logistic_model
2022-11-05                  4575  prophet_ZD_Net_logistic_model
2022-11-06                 12585  prophet_ZD_Net_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                          vertical
date                                                              
2019-11-01                   514  prophet_Chowhound_logistic_model
2019-11-02                   765  prophet_Chowhound_logistic_model
2019-11-03                   797  prophet_Chowhound_logistic_model
2019-11-04                   587  prophet_Chowhound_logistic_model
2019-11-05                   484  prophet_Chowhound_logistic_model
...                          ...                               ...
2022-11-02                   652  prophet_Chowhound_logistic_model
2022-11-03                   784  prophet_Chowhound_logistic_model
2022-11-04                   853  prophet_Chowhound_logistic_model
2022-11-05                   839  prophet_Chowhound_logistic_model
2022-11-06                   861  prophet_Chowhound_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                     vertical
date                                                         
2019-11-01                 34601  prophet_CNET_logistic_model
2019-11-02                 41344  prophet_CNET_logistic_model
2019-11-03                 46669  prophet_CNET_logistic_model
2019-11-04                 34670  prophet_CNET_logistic_model
2019-11-05                 33640  prophet_CNET_logistic_model
...                          ...                          ...
2022-11-02                  9187  prophet_CNET_logistic_model
2022-11-03                 18392  prophet_CNET_logistic_model
2022-11-04                  7903  prophet_CNET_logistic_model
2022-11-05                 11000  prophet_CNET_logistic_model
2022-11-06                  9342  prophet_CNET_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                           vertical
date                                                               
2019-11-01                    77  prophet_Giant_Bomb_logistic_model
2019-11-02                    83  prophet_Giant_Bomb_logistic_model
2019-11-03                   102  prophet_Giant_Bomb_logistic_model
2019-11-04                    77  prophet_Giant_Bomb_logistic_model
2019-11-05                    82  prophet_Giant_Bomb_logistic_model
...                          ...                                ...
2022-11-02                    69  prophet_Giant_Bomb_logistic_model
2022-11-03                    83  prophet_Giant_Bomb_logistic_model
2022-11-04                    72  prophet_Giant_Bomb_logistic_model
2022-11-05                    70  prophet_Giant_Bomb_logistic_model
2022-11-06                    83  prophet_Giant_Bomb_logistic_model

[1102 rows x 2 columns]

...

prophet_fcst_revenue                           vertical
date                                                               
2019-11-01                   143  prophet_Comic_Vine_logistic_model
2019-11-02                   161  prophet_Comic_Vine_logistic_model
2019-11-03                   175  prophet_Comic_Vine_logistic_model
2019-11-04                   148  prophet_Comic_Vine_logistic_model
2019-11-05                   153  prophet_Comic_Vine_logistic_model
...                          ...                                ...
2022-11-02                   126  prophet_Comic_Vine_logistic_model
2022-11-03                   138  prophet_Comic_Vine_logistic_model
2022-11-04                   134  prophet_Comic_Vine_logistic_model
2022-11-05                   136  prophet_Comic_Vine_logistic_model
2022-11-06                   134  prophet_Comic_Vine_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                   vertical
date                                                       
2019-11-01                   280  prophet_TV_logistic_model
2019-11-02                   360  prophet_TV_logistic_model
2019-11-03                   351  prophet_TV_logistic_model
2019-11-04                   285  prophet_TV_logistic_model
2019-11-05                   254  prophet_TV_logistic_model
...                          ...                        ...
2022-11-02                   294  prophet_TV_logistic_model
2022-11-03                   302  prophet_TV_logistic_model
2022-11-04                   265  prophet_TV_logistic_model
2022-11-05                   264  prophet_TV_logistic_model
2022-11-06                   252  prophet_TV_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                          vertical
date                                                              
2019-11-01                  9272  prophet_Game_Spot_logistic_model
2019-11-02                 46593  prophet_Game_Spot_logistic_model
2019-11-03                 47307  prophet_Game_Spot_logistic_model
2019-11-04                 50036  prophet_Game_Spot_logistic_model
2019-11-05                 10194  prophet_Game_Spot_logistic_model
...                          ...                               ...
2022-11-02                 66460  prophet_Game_Spot_logistic_model
2022-11-03                 91617  prophet_Game_Spot_logistic_model
2022-11-04                 16666  prophet_Game_Spot_logistic_model
2022-11-05                 28811  prophet_Game_Spot_logistic_model
2022-11-06                 12044  prophet_Game_Spot_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                           vertical
date                                                               
2019-11-01                  2741  prophet_Metacritic_logistic_model
2019-11-02                  2422  prophet_Metacritic_logistic_model
2019-11-03                  2180  prophet_Metacritic_logistic_model
2019-11-04                  2250  prophet_Metacritic_logistic_model
2019-11-05                  2309  prophet_Metacritic_logistic_model
...                          ...                                ...
2022-11-02                  2221  prophet_Metacritic_logistic_model
2022-11-03                  2320  prophet_Metacritic_logistic_model
2022-11-04                  2993  prophet_Metacritic_logistic_model
2022-11-05                  2440  prophet_Metacritic_logistic_model
2022-11-06                  1896  prophet_Metacritic_logistic_model

[1102 rows x 2 columns]

prophet_fcst_revenue                            vertical
date                                                                
2019-11-01                   583  prophet_Metrolyrics_logistic_model
2019-11-02                   581  prophet_Metrolyrics_logistic_model
2019-11-03                   601  prophet_Metrolyrics_logistic_model
2019-11-04                   537  prophet_Metrolyrics_logistic_model
2019-11-05                   503  prophet_Metrolyrics_logistic_model
...                          ...                                 ...
2021-10-30                   481  prophet_Metrolyrics_logistic_model
2021-10-31                   362  prophet_Metrolyrics_logistic_model
2021-11-01                   285  prophet_Metrolyrics_logistic_model
2021-11-02                   301  prophet_Metrolyrics_logistic_model
2021-11-03                   332  prophet_Metrolyrics_logistic_model

[734 rows x 2 columns]

In [ ]:
comp_dicts= {}
for key, value in fit_predict_dict.items():
  #print(key)
  #enter the range of dates below for the comp_summary function to flow through.  
  start_date = '2021-08'
  end_date = '2021-12'

  if key == 'prophet_B2B_logistic_model':
    comp_dict = pd.merge(value, B2B, left_on = value.index, right_on = B2B.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'

  if key == 'prophet_Media_Entertainment_logistic_model':
    comp_dict = pd.merge(value, Media_Entertainment, left_on = value.index, right_on = Media_Entertainment.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'

  if key == 'prophet_CNET_all_verticals_logistic_model':
    comp_dict = pd.merge(value, CNET_all_verticals, left_on = value.index, right_on = CNET_all_verticals.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'

  if key == 'prophet_Games_logistic_model':
    comp_dict = pd.merge(value, Games, left_on = value.index, right_on = Games.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
    

  if key == 'prophet_Game_FAQs_logistic_model':
    comp_dict = pd.merge(value, Game_FAQs, left_on = value.index, right_on = Game_FAQs.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
    

  if key == 'prophet_ZD_Net_logistic_model':
    comp_dict = pd.merge(value, ZD_Net, left_on = value.index, right_on = ZD_Net.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int)
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
    

  if key == 'prophet_Chowhound_logistic_model':
    comp_dict = pd.merge(value, Chowhound, left_on = value.index, right_on = Chowhound.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
      

  if key == 'prophet_CNET_logistic_model':
    comp_dict = pd.merge(value, CNET, left_on = value.index, right_on = CNET.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
   

  if key == 'prophet_Giant_Bomb_logistic_model':
    comp_dict = pd.merge(value, Giant_Bomb, left_on = value.index, right_on = Giant_Bomb.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
  

  if key == 'prophet_Download_logistic_model':
    comp_dict = pd.merge(value, Download, left_on = value.index, right_on = Download.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
   

  if key == 'prophet_TV_Guide_logistic_model':
    comp_dict = pd.merge(value, TV_Guide, left_on = value.index, right_on = TV_Guide.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
   

  if key == 'prophet_Comic_Vine_logistic_model':
    comp_dict = pd.merge(value, Comic_Vine, left_on = value.index, right_on = Comic_Vine.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
   

  if key == 'prophet_TV_logistic_model':
    comp_dict = pd.merge(value, TV, left_on = value.index, right_on = TV.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', ".com")
    comp_dict['fcst_type'] = 'prophet_logistic'
    

  if key == 'prophet_Game_Spot_logistic_model':
    comp_dict = pd.merge(value, Game_Spot, left_on = value.index, right_on = Game_Spot.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_logistic'
   

  if key == 'prophet_Metacritic_logistic_model':
    comp_dict = pd.merge(value, Metacritic, left_on = value.index, right_on = Metacritic.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
    

  if key == 'prophet_Metrolyrics_logistic_model':
    comp_dict = pd.merge(value, Metrolyrics, left_on = value.index, right_on = Metrolyrics.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_logistic_model', "")
    comp_dict['fcst_type'] = 'prophet_logistic'
    


  #else:
   # print('no matching dataframes')

  comp_dicts[key] = comp_dict
  


In [ ]:
for key, value in comp_dicts.items():
  display(key,  value, print('\n'))

'prophet_Game_FAQs_logistic_model'

prophet_fcst_revenue   revenue  difference  %_diff   vertical  \
date                                                                        
2021-08-31                 87424  68973.55    18450.45    0.27  Game FAQs   
2021-09-30                 87507  72694.79    14812.21    0.20  Game FAQs   
2021-10-31                 86368  70547.88    15820.12    0.22  Game FAQs   
2021-11-30                 85537  56946.70    28590.30    0.50  Game FAQs   
2021-12-31                108282  90877.31    17404.69    0.19  Game FAQs   

                   fcst_type  
date                          
2021-08-31  prophet_logistic  
2021-09-30  prophet_logistic  
2021-10-31  prophet_logistic  
2021-11-30  prophet_logistic  
2021-12-31  prophet_logistic

None

'prophet_ZD_Net_logistic_model'

prophet_fcst_revenue    revenue  difference  %_diff vertical  \
date                                                                       
2021-08-31                111506   97798.39    13707.61    0.14   ZD Net   
2021-09-30                126723  129140.92    -2417.92   -0.02   ZD Net   
2021-10-31                122136  146976.20   -24840.20   -0.17   ZD Net   
2021-11-30                192984  235114.10   -42130.10   -0.18   ZD Net   
2021-12-31                137205  139475.66    -2270.66   -0.02   ZD Net   

                   fcst_type  
date                          
2021-08-31  prophet_logistic  
2021-09-30  prophet_logistic  
2021-10-31  prophet_logistic  
2021-11-30  prophet_logistic  
2021-12-31  prophet_logistic

...

prophet_fcst_revenue   revenue  difference  %_diff    vertical  \
date                                                                         
2021-08-31                 58185  68523.57   -10338.57   -0.15  Metacritic   
2021-09-30                 82641  92035.88    -9394.88   -0.10  Metacritic   
2021-10-31                 69000  76471.83    -7471.83   -0.10  Metacritic   
2021-11-30                 65684  80419.14   -14735.14   -0.18  Metacritic   
2021-12-31                 89949  93975.84    -4026.84   -0.04  Metacritic   

                   fcst_type  
date                          
2021-08-31  prophet_logistic  
2021-09-30  prophet_logistic  
2021-10-31  prophet_logistic  
2021-11-30  prophet_logistic  
2021-12-31  prophet_logistic

None

'prophet_Metrolyrics_logistic_model'

prophet_fcst_revenue  revenue  difference  %_diff     vertical  \
date                                                                         
2021-08-31                 11133      0.0     11133.0     inf  Metrolyrics   
2021-09-30                 13184      0.0     13184.0     inf  Metrolyrics   
2021-10-31                 15523      0.0     15523.0     inf  Metrolyrics   
2021-11-30                   918      0.0       918.0     inf  Metrolyrics   

                   fcst_type  
date                          
2021-08-31  prophet_logistic  
2021-09-30  prophet_logistic  
2021-10-31  prophet_logistic  
2021-11-30  prophet_logistic

None

In [ ]:
# data output formatting
for key, value in comp_dicts.items():
  display(key,  value.drop(columns = ['difference',	'%_diff']), print('\n'))

'prophet_Game_FAQs_logistic_model'

prophet_fcst_revenue   revenue   vertical         fcst_type
date                                                                   
2021-08-31                 87424  68973.55  Game FAQs  prophet_logistic
2021-09-30                 87507  72694.79  Game FAQs  prophet_logistic
2021-10-31                 86368  70547.88  Game FAQs  prophet_logistic
2021-11-30                 85537  56946.70  Game FAQs  prophet_logistic
2021-12-31                108282  90877.31  Game FAQs  prophet_logistic

None

'prophet_ZD_Net_logistic_model'

prophet_fcst_revenue    revenue vertical         fcst_type
date                                                                  
2021-08-31                111506   97798.39   ZD Net  prophet_logistic
2021-09-30                126723  129140.92   ZD Net  prophet_logistic
2021-10-31                122136  146976.20   ZD Net  prophet_logistic
2021-11-30                192984  235114.10   ZD Net  prophet_logistic
2021-12-31                137205  139475.66   ZD Net  prophet_logistic

...

prophet_fcst_revenue   revenue    vertical         fcst_type
date                                                                    
2021-08-31                 58185  68523.57  Metacritic  prophet_logistic
2021-09-30                 82641  92035.88  Metacritic  prophet_logistic
2021-10-31                 69000  76471.83  Metacritic  prophet_logistic
2021-11-30                 65684  80419.14  Metacritic  prophet_logistic
2021-12-31                 89949  93975.84  Metacritic  prophet_logistic

None

'prophet_Metrolyrics_logistic_model'

prophet_fcst_revenue  revenue     vertical         fcst_type
date                                                                    
2021-08-31                 11133      0.0  Metrolyrics  prophet_logistic
2021-09-30                 13184      0.0  Metrolyrics  prophet_logistic
2021-10-31                 15523      0.0  Metrolyrics  prophet_logistic
2021-11-30                   918      0.0  Metrolyrics  prophet_logistic

None

## Linear Prophet

In [ ]:
fit_predict_dict = {}
for prophet_model_key in linear_prophet_model_dict.keys():
  model = linear_prophet_model_dict[prophet_model_key]
  #print(model)
  #print('\n')

  #create prediction dataframes with forward range of dates
  future_dates = model.make_future_dataframe(periods = 95, freq = "D")
  #display(future_dates)

  #cap and floor are used for logistic growth.  
  future_dates['cap'] = 200000
  future_dates['floor'] = 1000

  prophet_prediction = model.predict(future_dates)

  #making sure logistic takes all the negative values and returns absolute value, 
  prophet_prediction['yhat'] = prophet_prediction['yhat'].abs()

  prophet_prediction = prophet_prediction.astype(int)
  prophet_prediction['ds'] = pd.to_datetime(prophet_prediction['ds'])
  #print(f"******Summary for {prophet_model_key} prophet model ********",'\n')
  #display(prophet_prediction.tail(5))

  #plots
  print(f"******Summary graphs {prophet_model_key}********",'\n')
  display(plot_plotly(model, prophet_prediction, figsize=(3000,1000)))
  print('\n\n')
  display(plot_components_plotly(model, prophet_prediction,figsize=(3000,1000)))
  print('\n\n')

  print(f"******Summary for {prophet_model_key}********",'\n')
  prophet_prediction = prophet_prediction.reindex(['ds','yhat'], axis = 1)
  prophet_prediction.rename(columns={'ds':'date','yhat':'prophet_fcst_revenue'},inplace=True)

  prophet_prediction['vertical'] = prophet_model_key
  prophet_prediction.set_index('date', inplace = True)
  display(prophet_prediction.tail(5))
  
  fit_predict_dict[prophet_model_key]= prophet_prediction
  print('\n\n')

******Summary graphs prophet_Game_FAQs_linear_model******** 






******Summary for prophet_Game_FAQs_linear_model******** 



prophet_fcst_revenue                        vertical
date                                                            
2022-11-02                   802  prophet_Game_FAQs_linear_model
2022-11-03                   748  prophet_Game_FAQs_linear_model
2022-11-04                   764  prophet_Game_FAQs_linear_model
2022-11-05                  1313  prophet_Game_FAQs_linear_model
2022-11-06                  1589  prophet_Game_FAQs_linear_model




******Summary graphs prophet_ZD_Net_linear_model******** 






******Summary for prophet_ZD_Net_linear_model******** 



...




******Summary for prophet_Metacritic_linear_model******** 



prophet_fcst_revenue                         vertical
date                                                             
2022-11-02                  2304  prophet_Metacritic_linear_model
2022-11-03                  2341  prophet_Metacritic_linear_model
2022-11-04                  2697  prophet_Metacritic_linear_model
2022-11-05                  2496  prophet_Metacritic_linear_model
2022-11-06                  2463  prophet_Metacritic_linear_model




******Summary graphs prophet_Metrolyrics_linear_model******** 






******Summary for prophet_Metrolyrics_linear_model******** 



prophet_fcst_revenue                          vertical
date                                                              
2021-10-30                    97  prophet_Metrolyrics_linear_model
2021-10-31                    87  prophet_Metrolyrics_linear_model
2021-11-01                    65  prophet_Metrolyrics_linear_model
2021-11-02                    77  prophet_Metrolyrics_linear_model
2021-11-03                    76  prophet_Metrolyrics_linear_model

In [ ]:
comp_dicts= {}
for key, value in fit_predict_dict.items():
  #print(key)
  #enter the range of dates below for the comp_summary function to flow through.  
  start_date = '2021-08'
  end_date = '2021-12'

  if key == 'prophet_B2B_linear_model':
    comp_dict = pd.merge(value, B2B, left_on = value.index, right_on = B2B.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'

  if key == 'prophet_Media_Entertainment_linear_model':
    comp_dict = pd.merge(value, Media_Entertainment, left_on = value.index, right_on = Media_Entertainment.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'

  if key == 'prophet_CNET_all_verticals_linear_model':
    comp_dict = pd.merge(value, CNET_all_verticals, left_on = value.index, right_on = CNET_all_verticals.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'

  if key == 'prophet_Games_linear_model':
    comp_dict = pd.merge(value, Games, left_on = value.index, right_on = Games.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
    

  if key == 'prophet_Game_FAQs_linear_model':
    comp_dict = pd.merge(value, Game_FAQs, left_on = value.index, right_on = Game_FAQs.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
    

  if key == 'prophet_ZD_Net_linear_model':
    comp_dict = pd.merge(value, ZD_Net, left_on = value.index, right_on = ZD_Net.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int)
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
    

  if key == 'prophet_Chowhound_linear_model':
    comp_dict = pd.merge(value, Chowhound, left_on = value.index, right_on = Chowhound.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
      

  if key == 'prophet_CNET_linear_model':
    comp_dict = pd.merge(value, CNET, left_on = value.index, right_on = CNET.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
   

  if key == 'prophet_Giant_Bomb_linear_model':
    comp_dict = pd.merge(value, Giant_Bomb, left_on = value.index, right_on = Giant_Bomb.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
  

  if key == 'prophet_Download_linear_model':
    comp_dict = pd.merge(value, Download, left_on = value.index, right_on = Download.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
   

  if key == 'prophet_TV_Guide_linear_model':
    comp_dict = pd.merge(value, TV_Guide, left_on = value.index, right_on = TV_Guide.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
   

  if key == 'prophet_Comic_Vine_linear_model':
    comp_dict = pd.merge(value, Comic_Vine, left_on = value.index, right_on = Comic_Vine.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
   

  if key == 'prophet_TV_linear_model':
    comp_dict = pd.merge(value, TV, left_on = value.index, right_on = TV.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', ".com")
    comp_dict['fcst_type'] = 'prophet_linear'
    

  if key == 'prophet_Game_Spot_linear_model':
    comp_dict = pd.merge(value, Game_Spot, left_on = value.index, right_on = Game_Spot.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "").replace('_', " ")
    comp_dict['fcst_type'] = 'prophet_linear'
   

  if key == 'prophet_Metacritic_linear_model':
    comp_dict = pd.merge(value, Metacritic, left_on = value.index, right_on = Metacritic.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
    

  if key == 'prophet_Metrolyrics_linear_model':
    comp_dict = pd.merge(value, Metrolyrics, left_on = value.index, right_on = Metrolyrics.index, how = 'outer').drop(columns = ['ds','floor', 'cap']).rename(columns = {'y':'revenue', 'key_0':'date'})
    comp_dict = date_index(comp_dict)
    #comp_dict['revenue'] = comp_dict['revenue'].astype(int) 
    
    #print(f'\n comp_summary_{key}')
    #display(comp_summary(comp_dict, start_date,end_date))
    comp_dict =  comp_summary(comp_dict, start_date,end_date)
    comp_dict['vertical'] = key.replace('prophet_', "").replace('_linear_model', "")
    comp_dict['fcst_type'] = 'prophet_linear'
    


  #else:
   # print('no matching dataframes')

  comp_dicts[key] = comp_dict

In [ ]:
for key, value in comp_dicts.items():
  display(key,  value, print('\n'))

'prophet_Game_FAQs_linear_model'

prophet_fcst_revenue   revenue  difference  %_diff   vertical  \
date                                                                        
2021-08-31                 73950  68973.55     4976.45    0.07  Game FAQs   
2021-09-30                 70267  72694.79    -2427.79   -0.03  Game FAQs   
2021-10-31                 71772  70547.88     1224.12    0.02  Game FAQs   
2021-11-30                 67112  56946.70    10165.30    0.18  Game FAQs   
2021-12-31                 89749  90877.31    -1128.31   -0.01  Game FAQs   

                 fcst_type  
date                        
2021-08-31  prophet_linear  
2021-09-30  prophet_linear  
2021-10-31  prophet_linear  
2021-11-30  prophet_linear  
2021-12-31  prophet_linear

None

'prophet_ZD_Net_linear_model'

prophet_fcst_revenue    revenue  difference  %_diff vertical  \
date                                                                       
2021-08-31                125906   97798.39    28107.61    0.29   ZD Net   
2021-09-30                128937  129140.92     -203.92   -0.00   ZD Net   
2021-10-31                143715  146976.20    -3261.20   -0.02   ZD Net   
2021-11-30                193795  235114.10   -41319.10   -0.18   ZD Net   
2021-12-31                139966  139475.66      490.34    0.00   ZD Net   

                 fcst_type  
date                        
2021-08-31  prophet_linear  
2021-09-30  prophet_linear  
2021-10-31  prophet_linear  
2021-11-30  prophet_linear  
2021-12-31  prophet_linear

...

prophet_fcst_revenue   revenue  difference  %_diff    vertical  \
date                                                                         
2021-08-31                 73859  68523.57     5335.43    0.08  Metacritic   
2021-09-30                 84715  92035.88    -7320.88   -0.08  Metacritic   
2021-10-31                 74463  76471.83    -2008.83   -0.03  Metacritic   
2021-11-30                 83642  80419.14     3222.86    0.04  Metacritic   
2021-12-31                 97247  93975.84     3271.16    0.03  Metacritic   

                 fcst_type  
date                        
2021-08-31  prophet_linear  
2021-09-30  prophet_linear  
2021-10-31  prophet_linear  
2021-11-30  prophet_linear  
2021-12-31  prophet_linear

None

'prophet_Metrolyrics_linear_model'

prophet_fcst_revenue  revenue  difference  %_diff     vertical  \
date                                                                         
2021-08-31                  5983      0.0      5983.0     inf  Metrolyrics   
2021-09-30                  4521      0.0      4521.0     inf  Metrolyrics   
2021-10-31                  3366      0.0      3366.0     inf  Metrolyrics   
2021-11-30                   218      0.0       218.0     inf  Metrolyrics   

                 fcst_type  
date                        
2021-08-31  prophet_linear  
2021-09-30  prophet_linear  
2021-10-31  prophet_linear  
2021-11-30  prophet_linear

None

In [ ]:
# data output formatting
for key, value in comp_dicts.items():
  display(key,  value.drop(columns = ['difference',	'%_diff']), print('\n'))

'prophet_Game_FAQs_linear_model'

prophet_fcst_revenue   revenue   vertical       fcst_type
date                                                                 
2021-08-31                 73950  68973.55  Game FAQs  prophet_linear
2021-09-30                 70267  72694.79  Game FAQs  prophet_linear
2021-10-31                 71772  70547.88  Game FAQs  prophet_linear
2021-11-30                 67112  56946.70  Game FAQs  prophet_linear
2021-12-31                 89749  90877.31  Game FAQs  prophet_linear

None

'prophet_ZD_Net_linear_model'

prophet_fcst_revenue    revenue vertical       fcst_type
date                                                                
2021-08-31                125906   97798.39   ZD Net  prophet_linear
2021-09-30                128937  129140.92   ZD Net  prophet_linear
2021-10-31                143715  146976.20   ZD Net  prophet_linear
2021-11-30                193795  235114.10   ZD Net  prophet_linear
2021-12-31                139966  139475.66   ZD Net  prophet_linear

...

prophet_fcst_revenue   revenue    vertical       fcst_type
date                                                                  
2021-08-31                 73859  68523.57  Metacritic  prophet_linear
2021-09-30                 84715  92035.88  Metacritic  prophet_linear
2021-10-31                 74463  76471.83  Metacritic  prophet_linear
2021-11-30                 83642  80419.14  Metacritic  prophet_linear
2021-12-31                 97247  93975.84  Metacritic  prophet_linear

None

'prophet_Metrolyrics_linear_model'

prophet_fcst_revenue  revenue     vertical       fcst_type
date                                                                  
2021-08-31                  5983      0.0  Metrolyrics  prophet_linear
2021-09-30                  4521      0.0  Metrolyrics  prophet_linear
2021-10-31                  3366      0.0  Metrolyrics  prophet_linear
2021-11-30                   218      0.0  Metrolyrics  prophet_linear

None

## Neural Prophet

In [ ]:
CNET.reset_index()

day_dt         y         ds     cap  floor
0    2019-11-01  35082.77 2019-11-01  200000   1000
1    2019-11-02  32779.67 2019-11-02  200000   1000
2    2019-11-03  41536.35 2019-11-03  200000   1000
3    2019-11-04  37729.36 2019-11-04  200000   1000
4    2019-11-05  30692.96 2019-11-05  200000   1000
...         ...       ...        ...     ...    ...
1002 2022-07-30  18993.76 2022-07-30  200000   1000
1003 2022-07-31  18484.33 2022-07-31  200000   1000
1004 2022-08-01  17928.62 2022-08-01  200000   1000
1005 2022-08-02  17568.74 2022-08-02  200000   1000
1006 2022-08-03  16801.46 2022-08-03  200000   1000

[1007 rows x 5 columns]

In [ ]:
def neural_prophet(df):
  '''creates a neural prophet model against a loop of sites, date1 and 2 and for resampling
  - n forecasts are the number of forecasts into the future
  - nlags take a prior amount of days to predict next amount of days'''

  date1 = '2021-08'
  date2 = '2021-12'

  #n_lags defines whether the AR-Net is enabled (if n_lags > 0) or not. The value for n_lags is usually recommended to be greater than n_forecasts, 
  #if possible since it is preferable for the FFNNs to encounter at least n_forecasts length of the past in order to predict n_forecasts into the future. Thus, n_lags determine how far into the past the auto-regressive dependencies should be considered. 
  n_forecasts = 90
  n_lags = 95
  epochs = 125
  n_changepoints = 25


  #df = df.reset_index()
  df = df.drop(columns =['floor','cap'])

  #original model
  #neural_model = NeuralProphet(n_lags=2, ar_sparsity=0.5, num_hidden_layers = 2, d_hidden=20, learning_rate = 0.1, n_forecasts = n_forecasts, n_changepoints=n_changepoints, weekly_seasonality=False, daily_seasonality=False, yearly_seasonality=True)
  neural_model = NeuralProphet(n_lags=2,  num_hidden_layers = 2, d_hidden=20, learning_rate = 0.1, n_forecasts = n_forecasts, n_changepoints=n_changepoints, weekly_seasonality=False, daily_seasonality=False, yearly_seasonality=True)

  #neural_model = NeuralProphet(n_forecasts = n_forecasts, n_lags = n_lags, num_hidden_layers = 1, yearly_seasonality= True)

  #model = neural_model.fit(df.drop(columns = ['floor','cap']), freq="D")
  
  #model = neural_model.fit(df,freq = "D", epochs = 500 )
  neural_model.fit(df, freq = 'D', epochs = epochs)

  future_df = neural_model.make_future_dataframe(df,
                                                 #df.drop(columns = ['floor','cap']), 
                                                 periods = n_forecasts,
                                                 n_historic_predictions= True)
  


  predictions =neural_model.predict(future_df)

  #df_name = [x for x in globals() if globals()[x] is df][0] 
  #print("\n This is the model for: %s" % df_name)
  #plot.figure (figsize=(20,25))

  neural_model.plot(predictions);
  

  neural_model.plot_parameters();
  #print("\n This is the model for: %s" % df_name)
  
 
  predictions = predictions.rename(columns = {'y': 'revenue',  'ds':'date'})

  predictions = date_index(predictions)
  rev = predictions

  predictions = predictions.filter(regex = 'yhat')
  predictions = predictions.fillna(0).abs()
  rev = rev.revenue.fillna(0).astype(int)

  predictions['fcst'] = round(predictions.max(axis = 1),0)
  predictions['fcst'] = predictions.fcst.abs().fillna(0).astype(int)

  predictions = pd.merge(predictions, rev, how = 'inner', left_index = True, right_index = True)
  #predictions['vertical'] = df_name

  predictions = predictions.reindex(['fcst', 'revenue'], axis = 1)
  predictions = predictions.fillna(0)
  
  #predictions['revenue'] = predictions['revenue'].fillna(0).astype(int)

  predictions = predictions.loc[date1:date2].resample(rule = "M").sum()
  #predictions['vertical'] = df_name
  predictions['fcst_type'] = 'neural_prophet'

  return(predictions)


In [ ]:
neural_prophet_comp_dict = {}
for index, vertical in enumerate(site_splits):
  df_name = [x for x in globals() if globals()[x] is vertical][0] 
  print('This is the model for:',df_name, '\n')
  neural_prophet_comp_dict[f'neural_prophet_{site_splits_names[index]}'] = neural_prophet(vertical)
  #print('These are the charts for:',df_name, '\n')
  
  print('\n')

This is the model for: Game_FAQs 



TypeError: ignored

In [ ]:
#output dictionary

for key, value in neural_prophet_comp_dict.items():
    #df_name = [x for x in globals() if globals()[x] is df][0] 
    #print("\n This is the model for: %s" % df_name)
    value['vertical'] = key.replace('neural_prophet_', " ")
    value = value.reindex(['fcst', 'revenue', 'vertical', 'fcst_type'],axis = 1)
    display(key, print('\n'), value)
   

In [ ]:
#@title Neural Model Test

date1 = '2021-08'
date2 = '2021-12'

#with complicated model parematers we end up with a matrix with new yhats in new columns..so need to take the values and place into single column  
n_forecasts = 10
n_lags = 60
epochs = 10
n_changepoints = 25
batch_size = 2

  #df = df.reset_index()
df = CNET.drop(columns =['floor','cap'])
#df = CNET

  #original model
#neural_model = NeuralProphet()#seasonality_mode ='multiplicative')
neural_model = NeuralProphet(n_lags=2, ar_sparsity=0.5, num_hidden_layers = 2, d_hidden=20, learning_rate = 0.1, n_forecasts = n_forecasts, n_changepoints=n_changepoints,weekly_seasonality=False, daily_seasonality= False, yearly_seasonality=True)
#neural_model.add_events(holidayz)
#neural_model = NeuralProphet(n_forecasts = n_forecasts, n_lags = n_lags, num_hidden_layers = 1)

  #model = neural_model.fit(df.drop(columns = ['floor','cap']), freq="D")
  
  #model = neural_model.fit(df,freq = "D", epochs = 500 )
neural_model.fit(df, freq = 'D', epochs = epochs)

future_df = neural_model.make_future_dataframe(df,
                                                 #df.drop(columns = ['floor','cap']), 
                                                 periods = n_forecasts,
                                                 n_historic_predictions= True)

predictions =neural_model.predict(future_df)


df_name = [x for x in globals() if globals()[x] is df][0]  
print("\n This is the model for: %s" % df_name)


neural_model.plot(predictions);
  

neural_model.plot_parameters();
predictions = date_index(predictions)
predictions = predictions.filter(regex = 'yhat').tail(12)
predictions['fcst'] = round(predictions.max(axis = 1),0)
predictions['fcst'] = predictions.fcst.abs()
predictions['vertical'] = df_name

#predictions['row_sum'] = predictions.fillna(0).sum(axis = 1)
#predictions['row_sum'] = predictions.row_sum.astype(int)

pd.set_option('display.max_rows', None)
#yhats = [col for col in predictions.columns if 'ds'in col]
#predictions = date_index(predictions)
predictions.tail(12)

predictions = predictions.filter(regex = 'yhat').tail(12)
predictions['fcst'] = round(predictions.max(axis = 1),0)
predictions


In [ ]:
#sites = list(df.report_site_nm.unique())

#for site in sites:
#    '''to call a site...CNET'''
#    globals()[str(site).replace(" ","_")] = prophet_site_split(site) 





neural_prophet_model_dict = {}

#vertical_splits
#for index, vertical in enumerate(vertical_splits):

#site_splits
for index, vertical in enumerate(site_splits):



    neural_model = NeuralProphet( n_lags=24,
    ar_sparsity=0.5,
    num_hidden_layers = 2,
    d_hidden=20,
    learning_rate = 0.1)
   




    #create prediction dataframes with forward range of dates
    #future_dates = model.make_future_dataframe(periods = 95, freq = "D")
    
    

    #vertical_split dict, need to select this line or line below.  depends if forecasting for verticals or individual sites
    #prophet_model_dict[f'prophet_{vertical_splits_names[index]}_model'] = model.fit(vertical)

    #site split dict
    
    neural_prophet_model_dict[f'prophet_{site_splits_names[index]}_neural_model'] = neural_model.fit(vertical.drop(columns = ['floor','cap']), validate_each_epoch=True, valid_p=0.2, freq='D', plot_live_loss=True, epochs=10)


    #prophet_prediction = model.predict(future_dates)
  
    #prophet_prediction = prophet_prediction.astype(int)
    #prophet_prediction['ds'] = pd.to_datetime(prophet_prediction['ds'])
    #print(f"******Summary for {vertical.keys()} prophet model ********",'\n')
    #display(prophet_prediction.tail(5))



In [ ]:
#neural model dict summary 

print ("Dict key-value within neural prophet_model_dict are : ")
for key, value in neural_prophet_model_dict.items():
  display (key,print('\n'), value)

In [ ]:
for prophet_model_key in neural_prophet_model_dict.keys():
  neural_model = neural_prophet_model_dict[prophet_model_key]
  print(neural_model)
  #future_dates = neural_model.make_future_dataframe(prophet_model_key, n_historic_prediction = len(prophet_model_key), periods = 90)

In [ ]:
fit_predict_dict = {}
for prophet_model_key in neural_prophet_model_dict.keys():
  model = neural_prophet_model_dict[prophet_model_key]
  #print(model)
  #print('\n')

  #create prediction dataframes with forward range of dates, original line
  #future_dates = model.make_future_dataframe(periods = 95, freq = "D")

  #future_dates = model.make_future_dataframe(prophet_model_key, n_historic_prediction = True)




  #display(future_dates)

  #cap and floor are used for logistic growth.  
  #future_dates['cap'] = 200000
  #future_dates['floor'] = 1000

  prophet_prediction = model.predict(prophet_model_key)

  #making sure logistic takes all the negative values and returns absolute value
  #prophet_prediction['yhat'] = prophet_prediction['yhat'].abs()

  #prophet_prediction = prophet_prediction.astype(int)
  #prophet_prediction['ds'] = pd.to_datetime(prophet_prediction['ds'])
  #print(f"******Summary for {prophet_model_key} prophet model ********",'\n')
  #display(prophet_prediction.tail(5))

  #plots
  print(f"******Summary graphs {prophet_model_key}********",'\n')
  display(plot_plotly(model, prophet_prediction, figsize=(3000,1000)))
  print('\n\n')
  display(plot_components_plotly(model, prophet_prediction,figsize=(3000,1000)))
  print('\n\n')

  print(f"******Summary for {prophet_model_key}********",'\n')
  prophet_prediction = prophet_prediction.reindex(['ds','yhat'], axis = 1)
  prophet_prediction.rename(columns={'ds':'date','yhat':'prophet_fcst_revenue'},inplace=True)

  prophet_prediction['vertical'] = prophet_model_key
  prophet_prediction.set_index('date', inplace = True)
  display(prophet_prediction.tail(5))
  
  fit_predict_dict[prophet_model_key]= prophet_prediction
  print('\n\n')

In [ ]:
NeuralProphet.make_future_dataframe()

In [ ]:
x

# Arima Modeling

In [ ]:
verticals = list(df2.vertical.unique())
sites = list(df2.report_site_nm.unique())


def arima_vertical_split(bu):
    '''creates a seperate df for each business unit in verticals. keeps only numerical columns and resamples for daily groupings'''
    #split_df = df[df['vertical'] == bu].select_dtypes(include = ['float64'])
    split_df = df2[df2['vertical'] == bu].resample(rule = 'D').sum()
    #split_df = df.resample(rule = 'D').sum()
    
    return split_df

    
for bu in verticals:
    '''to call a vertical...B2B'''
    globals()[str.lower((bu).replace("&","_"))] = arima_vertical_split(bu)
    


def arima_site_split(site):
    '''creates a seperate df for each business unit in verticals. keeps only numerical columns and resamples for daily groupings'''
    #split_df = df[df['vertical'] == bu].select_dtypes(include = ['float64'])
    split_df = df2[df2['report_site_nm'] == site].resample(rule = 'D').sum()
    #split_df = df.resample(rule = 'D').sum()
    
    return split_df

    
for site in sites:
    '''to call a site...CNET'''
    globals()[str.lower((site).replace(" ","_"))] = arima_site_split(site)   

In [ ]:
CNET

In [ ]:
cnet

In [ ]:
vertical_splits_names  = list(map(lambda x:x.lower(),vertical_splits_names))
site_splits_names = list(map(lambda x:x.lower(),site_splits_names))

site_splits = [game_faqs, zd_net, chowhound, cnet, giant_bomb, download, tv_guide, comic_vine, tv, game_spot, metacritic, metrolyrics]
vertical_splits = [b2b, media_entertainment, cnet_all_verticals, games]


In [ ]:
x

In [ ]:
#creation of arima models.  Will loop through vertical/site splits list.  Name is assigned using vertical_split_names list.  The order of vertical splits and vertical split names must be in the same order

#arima_model_dict = {}
#for index, vertical in enumerate(site_splits):
#    arima_model_dict[f'auto_arima_{site_splits_names[index]}_model'] = auto_arima(vertical, start_p = 0, start_q = 0, max_p = 365, max_q = 365,start_P = 0, start_Q = 0, max_P = 5, max_Q = 5,m = 12, seasonal = True, trace = True, start_d = 0, max_D = 5, error_action = 'warn', supress_warnings = True, stepwise = True, random_state = 20, n_fits = 30, n_jobs = -1);
    print("\n\n")

In [ ]:
#Summary and aic prints
for key in arima_model_dict.keys():
    print(f"******Summary for {key} arima model ********")
    print(arima_model_dict[key].summary())
    
    
    #print("\n\n\n\n")
    #f is called formatting strings
    #print("******AIC value for {}******".format(key))
    print(f"****AIC value for {key}*****")    
    #print("\n")
    print(display(arima_model_dict[key].aic().round(0)))
    print("\n\n\n\n")

In [ ]:
arima_model_dict

In [ ]:
cnet

In [ ]:
train_start_date = '2019-11-01'
train_end_date = '2021-08-31'
test_start_date = str(pd.to_datetime(train_end_date) +timedelta(1))

n_input = 180
n_features = 1

epochs = 10

def lstm(df):

  results = seasonal_decompose(df['revenue'])
  results.plot();

  scaled_train = df.loc['2019-11-01' : '2021-08-31']
  scaled_test = df.loc['2021-09-01':]

  #convert scale from 0-1
  scaler = MinMaxScaler()

  scaler.fit(train)
  scaled_train = scaler.transform(train)
  scaled_test = scaler.transform(test)

  generator = TimeseriesGenerator(scaled_train, scaled_train, length = n_input, batch_size = 1)

  X,y = generator[0]
  #we should see a flatten aray of 30 inputs and 1 prediction(y)

  display(X.shape, y.shape)

  #define model
  model = Sequential()
  model.add(LSTM(100, activation = 'relu', input_shape = (n_input, n_features)))
  model.add(Dense(1))
  model.compile(optimizer = 'adam', loss = 'mse')

  display(model.summary())

  #fit model
  model.fit(generator, epochs = epochs)

  loss_per_epoch = model.history.history['loss']
  plt.plot(range(len(loss_per_epoch)), loss_per_epoch)


  test_predictions = []

  first_eval_batch = scaled_train[-n_input:]
  current_batch = first_eval_batch.reshape((1,n_input, n_features))

  for i in range(len(test)):
      
      #get the prediction value for the first batch, use last set of values in order to make a prediction and storing as current pred 
      current_pred = model.predict(current_batch)[0]
      
      #append the predictions into the array, from current pred
      test_predictions.append(current_pred)
      
      #use the prediction to update the batch and remove the first value, dropping first input, making next prediction, getting new input and the cycle continues, axis = 1 will append to column
      current_batch = np.append(current_batch[:,1:,:], [[current_pred]], axis = 1)
      
      
  #test_predictions    

  #need to transform back into the original scale, currently between 0-1 using the Min Max scaler
  true_predictions = scaler.inverse_transform(test_predictions) 
  #append the true predictions back into the original test set
  test['lstm'] = true_predictions

  display(test.plot(figsize = (12,6)))


